In [29]:
# Run in terminal or command prompt
# python3 -m spacy download en

import numpy as np
import pandas as pd
import re, nltk, spacy, gensim

# Sklearn
from sklearn.decomposition import LatentDirichletAllocation, TruncatedSVD
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.model_selection import GridSearchCV
from pprint import pprint
from googletrans import Translator

In [28]:
!pip install googletrans

  Stored in directory: C:\Users\v-savrav\AppData\Local\pip\Cache\wheels\50\d6\e7\a8efd5f2427d5eb258070048718fa56ee5ac57fd6f53505f95
Successfully built googletrans


In [87]:
df = pd.concat(pd.read_excel("C:\\Users\\v-savrav\\Documents\\SampleDataset2.xlsx", sheet_name=None), ignore_index=True)

In [88]:
df=df[1:50]
import nltk
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
#stop_words.extend(['from', 'subject', 're', 'check','apars_apar','error'])
#stop_words.extend(['close','let','hour','know','good','need','subject','desk','find', 'name','thank','thanks','send','com','prohelp','regards','regard','information','message','team'
 #                  ,'mail','check','apars_apar','error','www','hi','cc','sent','date','use','try','query','intend','contain','recipient','request','hour','number'])

In [89]:
df['description']

1     Hi AP,Please discard the email below and use t...
2     Hi Team, Please find correction docs for your ...
3     Hello Prohelp and US AP Escalations <usapesc@m...
4     Hi team, I’m attaching 3 invoices from Wunderm...
5     Please find attached the Invoice and POE for P...
6     Hi Prohelp-  I’m wondering if you could direct...
7     It does thankyou&#128522;  Many thanks Helen  ...
8     Thank you Kiran!  Sorry but I do not understan...
9     Hea klient Kirjaga on kaasas PDF-formaadis arv...
10    You don't often get email from PETE.KINGETT@AC...
11    Hi Prohelp, The following invoices were submit...
12    Sehr geehrte Damen und Herren,  als Anlage erh...
13    Estimados espero se encuentren bien!   Necesit...
14    Med venlig hilsen  Hahnemanns Køkken ApS regns...
15    Hi Team,  We have received below error while s...
16    7601542227  Here is the invoice, for the 4th t...
17    Hi,  I’m trying to approve this but I get the ...
18    Dear PO Box and AP teams, Can you please r

In [90]:
# Convert to list
data = df["description"].values.tolist()

def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

print(data_words[:1])

TypeError: 'str' object is not callable

In [100]:
print(data_words[:1])

[['hi', 'team', 'please', 'cancel', 'the', 'first', 'submission', 'of', 'er', 'as', 'the', 'incorrect', 'receipts', 'were', 'attached', 'however', 'am', 'now', 'going', 'to', 'submit', 'the', 'correct', 'receipts', 'to', 'the', 'er', 'thank', 'you', 'regards', 'renee', 'bradshaw']]


In [101]:
data_words

[['hi',
  'team',
  'please',
  'cancel',
  'the',
  'first',
  'submission',
  'of',
  'er',
  'as',
  'the',
  'incorrect',
  'receipts',
  'were',
  'attached',
  'however',
  'am',
  'now',
  'going',
  'to',
  'submit',
  'the',
  'correct',
  'receipts',
  'to',
  'the',
  'er',
  'thank',
  'you',
  'regards',
  'renee',
  'bradshaw'],
 ['hi',
  'ap',
  'please',
  'discard',
  'the',
  'email',
  'below',
  'and',
  'use',
  'this',
  'po',
  'for',
  'urn',
  'regards',
  'poboxfrom',
  'po',
  'box',
  'nfe',
  'sent',
  'friday',
  'june',
  'pm',
  'to',
  'gunaseelan',
  'jayaraj',
  'gujaya',
  'microsoft',
  'com',
  'cc',
  'po',
  'box',
  'nfe',
  'nfebr',
  'microsoft',
  'com',
  'subject',
  'fw',
  'regarding',
  'po',
  'number',
  'hi',
  'ap',
  'follows',
  'po',
  'regards',
  'pobox',
  'from',
  'po',
  'box',
  'nfe',
  'sent',
  'friday',
  'june',
  'pm',
  'to',
  'angela',
  'domingues',
  'moreira',
  'adecco',
  'recursos',
  'humanos',
  'angdom',
 

In [91]:
def remove_stopwords(texts):
    return [[word for word in gensim.utils.simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

data_words_nostops = remove_stopwords(data_words)

In [97]:
data_words_nostops[5]

['please',
 'find',
 'attached',
 'invoice',
 'poe',
 'po',
 'dads',
 'grads',
 'invoice',
 'total',
 'tax',
 'total',
 'invoice',
 'inclusive',
 'taxes',
 'please',
 'upload',
 'ms',
 'invoice',
 'include',
 'poe',
 'wm',
 'canada',
 'whitelisted',
 'ap',
 'canada',
 'complete',
 'paul',
 'paul',
 'harris',
 'national',
 'channel',
 'executive',
 'microsoft',
 'canada',
 'inc',
 'paulharr',
 'microsoft',
 'com',
 'office',
 'gamertag',
 'apau',
 'calypse',
 'bring',
 'business',
 'cloud',
 'microsoft',
 'azure',
 'https',
 'azure',
 'microsoft',
 'com',
 'en',
 'us',
 'blog']

In [92]:
def lemmatization(texts, allowed_postags=['NOUN']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append(" ".join([token.lemma_ if token.lemma_ not in ['-PRON-'] else '' for token in doc if token.pos_  not in allowed_postags]))
    return texts_out

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# Run in terminal: python3 -m spacy download en
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])
#nlp = spacy.load("en_core_web_sm")
# Do lemmatization keeping only Noun, Adj, Verb, Adverb
data_lemmatized = lemmatization(data_words_nostops, allowed_postags=['NOUN'])

print(data_lemmatized[:3])

['hi please cancel first er incorrect attach however go submit correct er thank', 'hi ap please discard po urn regard po box nfe send friday june pm gunaseelan jayaraj gujaya microsoft com cc po box nfe nfebr microsoft com subject fw regard po hi ap follow po regard pobox po box nfe send friday june pm angela domingues moreira adecco recursos humanos angdom microsoft com subject fw regard po segue po obrigadodanilo gimenez service brazil danilo docuprint com br office skype dgimenez dek web www docuprint avenida fagundes de oliveira unidade piraporinha cep diadema sao paulo de po box nfe mailto nfebr microsoft enviada  sexta feira de junho de para jean carlos valeriano de araujo danilo docuprint com br cc po box nfe nfebr microsoft com assunto fw regard po danilo boa tarde po informada para fatura  anexo nao valida por gentileza informar po correta att pobox po box nfe send thursday june pm angela domingues moreira adecco recursos humanos angdom microsoft com subject fw regard po po gu

In [107]:
print(data_lemmatized[7])

thankyou many helen anji reddy accenture send june helen rudge brook street helrud microsoft com ms uk accounts payable apuk microsoft com priya paramakudi rajagopal accenture pparam microsoft com cc ap uki escalation apuki microsoft com tom chilton connor tchilton microsoft com leftley brook street wileft microsoft com william leftley willef microsoft com subject tkt po close hi helen payment vendor take july budget hit fy fy question regard anji reddy account payable chennai microsoft accenture operations anjpa microsoft com one one helen rudge brook street send friday june pm ms uk account payable apuk microsoft com priya paramakudi rajagopal accenture pparam microsoft com cc anji reddy accenture anjpa microsoft com anji reddy accenture anjpa microsoft com ap uki escalation apuki microsoft com tom chilton connor tchilton microsoft com leftley brook street wileft microsoft com william leftley willef microsoft com subject tkt po close hi joel say process take record despite due physic

In [102]:
data_words_lemm = list(sent_to_words(data_lemmatized))

TypeError: 'str' object is not callable

In [9]:
Expense_Report	"	EMP number ,reimbursement,Last WorkingDay ,Final Working day,EOS,End of settlement,ER,expense,MS authorize,Audit ,final status of claim,submitting my claim,submiting my expense,MS expense, MS expense 1.0, MS expense 2.0,MS expense ,MyExpense,Expense Report,Credit Card payment,My card payment,Meal Expense,Flight Charge,Flight expense,Last Travel expense,Meals,Audit,Audit inquiries,Airport drop,T&E,Amex Card payment,TE
Disbursement	Failed payment,rejected,citi bankquery,refund entry,bank GL clearning,proof of payment,reverse 1500, idoc,run id,citibank account,bank rejection, CI refund,bank rejection reason,payment return,rejection reason,custom duty,bank GL posting

data_words_lemm[1]

['discard',
 'regard',
 'follow',
 'regard',
 'regard',
 'regard',
 'regard',
 'kindly',
 'provide',
 'valid']

In [17]:
def check(sentence, words): 
    res = [all([k in s for k in words]) for s in sentence] 
    return [sentence[i] for i in range(0, len(res)) if res[i]] 
      


In [109]:
words = ["microsoft","payment central","APMDG","AP MDG","cr ","change request","mdg" ,"bank account change","new vendor creation" ,"payment terms change" ,"vendor block","vendor email/fax","request id "]
invoice=["urn","po","purchase order","reference number","enclosed","invoice","attach invoice","tds" ,"rectification" ,"With hold tax","staus of invoice","enclosed","emitance advice" ,"payment status"]

for sentence in data_lemmatized:
    print(sentence)
    print(check(sentence, invoice)) 

hi please cancel first er incorrect attach however go submit correct er thank
[]
hi ap please discard po urn regard po box nfe send friday june pm gunaseelan jayaraj gujaya microsoft com cc po box nfe nfebr microsoft com subject fw regard po hi ap follow po regard pobox po box nfe send friday june pm angela domingues moreira adecco recursos humanos angdom microsoft com subject fw regard po segue po obrigadodanilo gimenez service brazil danilo docuprint com br office skype dgimenez dek web www docuprint avenida fagundes de oliveira unidade piraporinha cep diadema sao paulo de po box nfe mailto nfebr microsoft enviada  sexta feira de junho de para jean carlos valeriano de araujo danilo docuprint com br cc po box nfe nfebr microsoft com assunto fw regard po danilo boa tarde po informada para fatura  anexo nao valida por gentileza informar po correta att pobox po box nfe send thursday june pm angela domingues moreira adecco recursos humanos angdom microsoft com subject fw regard po po guna

invoice th please prioritize andres ms ireland account payable send friday june ebru erol yildirim consulting meerol microsoft com cc andres valencia andres valencia microsoft com paul schuman pschuman microsoft com paul schuman pschuman microsoft com subject tkt hi thank request provide open process let  know query regard kiran microsoft one europe account payable feel get within acceptable timeframe inadequate please escalate ap uki escalation apuki microsoft check invoice status try need urgent try cim one stop portal query internal microsoft use original erol yildirim receive fri jun gmt india standard apie ireland cc andres valencia paul schuman paul schuman subject tkt fw hi eur still open po show po also miss invoice need hit fy go accrual ebrufrom ms ireland account payable send wednesday june andres valencia andres valencia microsoft com cc christina leufroy consulting chrleu microsoft com ebru erol yildirim consulting meerol microsoft paul schuman pschuman microsoft com paul 

hi could please validate adjust report do end walter souza accenture microsoft one brazil buenos argentina wasouz microsoft com daiana gamarra accenture send wednesday january pm ms brazil ap brzap microsoft com makendran accenture makenb microsoft com cc ana paula rocha moura tmf anaroc microsoft com jose carlos junior jojuni microsoft com martin hage accenture mahag microsoft com maria cecilia napolitano marit microsoft com michelle santos tmf brasil servicos administra sanmic microsoft com roberta alves barbosa tmf brasil servicos administra roalve microsoft gisele marques tmf brasil assessoria contabil gimarq microsoft matias lunatti accenture maluna microsoft com agustin erize accenture ageriz microsoft com vanessa saggioratto tmf brasil servicos administra vasagg microsoft com susan queiroz da silva tmf brasil servicos administra suquei microsoft com elina beltramino accenture elbelt microsoft com subject pendencias high hi please need adjust inform previus pende make donot hesit

hello follow await could advise please validate po functionsummary execfunc current po doc vendor mm doc ms invoice total commercial commercial field rodopin alinea europe pin executive de chirag ve envoye vendredi juin anke tomkiewicz hvs anket microsoft bulkens abulkens microsoft daryl yeap adecco dyeap microsoft com georgia heath adecco geheat microsoft com julie norden ifg international financial gr junord microsoft com marc gubler manpower ag zug magubl microsoft com marte høvik venezu mahvik microsoft com maria cabillan randstad canada group marcab microsoft mieko uozu recruit staff miekou microsoft com matthew shaw brook street mshaw microsoft com anais harmant anaisha microsoft com namitha mathews adecco limit namath microsoft com anita pepene anita pepene microsoft com anne stoll astoll microsoft com tessa connolly brook street teconn microsoft com ayumi kaihatsu ayumi kaihatsu microsoft com bill danna bill danna microsoft com bessie chu bechu microsoft com brett gordon brettg

ms ap please check attach po monocept send hard th june see ms invoice dear raghava ap confirm invoice valid still need submit per microsoft valid timely agree sow send directly microsoft bifpmo contact ponnambalam nee send bifpmo microsoft state standard microsoft attach please sun tv get fill send date clearly mention regard nitin santosh microsoft azure microsoft corp india pvt ltd ground st floor signature build domlur bangalore nitin santosh microsoft phone raghava prasad mailto rp monocept com send friday june pm nitin santosh nitin santosh microsoft com cc monocept account account monocept microsoft po sun tv poc hard require sow send th june attach logical do th june also loop email good regard raghava prasad monocept digital architect future us ny city india hyderabad gurgaon http linkedin https linkedin raghavaprasad member institute computer sciences social informatics nitin santosh mailto nitin santosh microsoft send friday june pm raghava prasad rp monocept monocept accoun

...

hi jackie receive invoice yet ap try barton procurement services contractor microsoft office jabart microsoft com microsoft procurement subsequent emails topic set fully execute legally bind may contain confidential share third without prior write microsoft intend sender immediately microsoft limited company register england wales whose registered microsoft thames valley park reading rg wg jasvir barton brook street send june jackie tan jackie tan tes amm com jackie tan jackie tan tes amm com lusia wahyu quadra lwahyu microsoft com ms indonesia ap apid microsoft com wang chunmei accenture wangch microsoft com cc grp microsoft sg microsoft sg tes amm com subject tkt indonesia credit te add need close fiscal ap please see attach ca next ms ap provide jackie invoice tes indonesia wire need routed corp gl io fund corp need route post appreciate barton procurement services contractor microsoft office jabart microsoft com microsoft procurement subsequent emails topic set fully execute agree


hello razia kindly regard sowbar sadhik accenture microsoft one nepa records accenture outsource support microsoft chennai one one razia raja mohammed accenture send thursday june pm ms lebanon record reclb microsoft com cc bharathi ramani accenture bhrama microsoft com jothi prakasam accenture jothip microsoft com ragul ganesh accenture ragga microsoft com chandrasekaran ramasamy chram microsoft com velmurugan annamalai accenture velann microsoft com deepika mahapatra accenture demaha microsoft com kusumeswar katreddi accenture kukatr microsoft com ramyaa rathen microsoft com subject dummy vat report lebanon hello dummy vat report share rd july since belong regard razia payable global nepa microsoft accenture outsource chennai india check invoice status try need urgent try cim one stop portal query internal microsoft use ms mea payable commit within meet inadequate may escalate mailbox sla apmea microsoft com ms lebanon record send thursday june pm ms lebanon ap aplb microsoft razia r

hello still hold shawn de apie ireland mailto apie microsoft com envoye vendredi juin lalla fofana lalla ftf sn objet tkt profil de paiement close dear full ap resolve reference tkt trust assist resolvedthe please complete short tell  support take please use close need pick remove send respective ap alias
[]
hi kindly clear dd gl cc io dd _ athlonthank regard minnal
[]
hi dfs please provide brl attach good regard marcelo gonzalez adecco behalf microsoft treasury brazil finance marcde microsoft com alexandre fernandes send monday july marcelo de oliveira gonzalez adecco recursos humanos marcde microsoft com cc takahashi glauce nokia br sao paulo glauce takahashi nokia com subject deposito microsoft mobile bom dia oi glauce tudo bem sim vc vou ajuda ao da tesouraria marcelo por favor vc consegue nos ajudar com informacao abaixo muito obrigado alexandre takahashi glauce nokia br sao paulo mailto glauce takahashi nokia com send segunda feira de julho de alexandre fernande alexandre fernand

hello sriganth kindly please clear post bank hungary please confirm donethank much regard elena elena bradistilova accenture outsource support microsoft onefinance warsaw elenab microsoft com one one elena bradistilova accenture send friday june pm sriganth selvanambi accenture srselv microsoft com ms hungary ap aphu microsoft cc iwona danielczyk accenture iwdani microsoft com subject bank clearing hungary hello shriganth bank hungary clear please clear
[]
hello could please provide follow make clear post key doc due outgoing thank vaishali jadal xtreme consulting group inc support askcela business technical mon fri pm
[]
lydia li details hong kong citibank branch code transaction great hkd transaction hkd familiar microsoft hong kong limited nonref please reply monitor incoming direct sincerely citibank
[]
hi chris see send another include see assist please assist chris send another try actual still owe never cash look appear make amount code check sap account doc ms sap clear doc pay

hi please follow  ach ctx contain addenda records arun pandian paarun microsoft com accounts payable outsource support microsoft chennai india one one save switch always
[]
hi sir madam check bank receive yet accord first issue via take hit would please help check kind br peter tue jun pm peter su petitpj gmail write hi sir madam receive many check next support regard peteron tue jun prohelp  ap prohelp microsoft write hi peter thank could see issue via take hit let  know query jeevakumar microsoft one  account payable feel get within acceptable timeframe inadequate please escalate  ap escalations usapesc microsoft com check invoice status try ms invoice need urgent try cim one stop portal query internal microsoft use original receive mon jun gmt india standard jacob kehle jacob kehle prohelp  ap prohelp  ap cc fgodisb mingming subject tkt antn vmf rej twd hi jacob prohelp team check bank still receive swift code hsbctwtp name bank su chen hao since prohelp  say release june th could h

In [112]:
#search_list  = ["Payment central","APMDG","AP MDG","CR #","change request","MDG" ,"bank account ","new vendor creation" ,"payment terms change" ,"vendor block","vendor email/fax","request id "]
search_list  =["urn","po","Purchase order","reference number","enclosed","invoice","attached","tds" ,"rectification" ,"With hold tax","staus of invoice","enclosed","emitance advice" ,"payment status","invoice Tool","POE","PO extension#","MS invoice#","Attached EI file,EI upload,remittance,partner invoice,microsoft PO,vendor ID,invoice #,reference #,following invoice #,statement of account,upload the attached file,check #,cheque #,DD #,Tax payment ,supplier #,



In [113]:
print(search_list)

['urn', 'po', 'Purchase order', 'reference number', 'enclosed', 'invoice', 'attached', 'invoice', 'tds', 'rectification', 'With hold tax', 'staus of invoice', 'enclosed', 'emitance advice', 'payment status']


In [115]:
for long_string in data_lemmatized:
       #for number in list:
    #print(long_string)
    if re.compile('|'.join(search_list),re.IGNORECASE).search(long_string): #re.IGNORECASE is used to ignore case
        # Do Something if word is present    
        print("present")
        print(long_string)
    else:
        print("no")
    print("-----------")
    # Do Something else if word is not present

no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
no
-----------
no
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
no
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
pre

search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
no
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
no
-----------
no
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
no
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
searc

-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
no
-----------
present
search_list
-----------
no
-----------
no
-----------
no
-----------
present
search_list
-----------
no
-----------
no
-----------
present
search_list
-----------
no
-----------
no
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
no
-----------
present
search_list
-----------
present
search_

search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
no
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
-----------
no
-----------
no
-----------
no
-----------
present
search_list
-----------
no
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
present
search_list
-----------
no
--------

In [117]:
for long_string in data_lemmatized:
       #for number in list:
    #print(long_string)
    if re.compile('|'.join(search_list),re.IGNORECASE).search(long_string): #re.IGNORECASE is used to ignore case
        # Do Something if word is present    
        print("Invoice")
        print(long_string)
    else:
        print("no")
    print("-----------")
    # Do Something else if word is not present

no
-----------
Invoice
hi ap please discard po urn regard po box nfe send friday june pm gunaseelan jayaraj gujaya microsoft com cc po box nfe nfebr microsoft com subject fw regard po hi ap follow po regard pobox po box nfe send friday june pm angela domingues moreira adecco recursos humanos angdom microsoft com subject fw regard po segue po obrigadodanilo gimenez service brazil danilo docuprint com br office skype dgimenez dek web www docuprint avenida fagundes de oliveira unidade piraporinha cep diadema sao paulo de po box nfe mailto nfebr microsoft enviada  sexta feira de junho de para jean carlos valeriano de araujo danilo docuprint com br cc po box nfe nfebr microsoft com assunto fw regard po danilo boa tarde po informada para fatura  anexo nao valida por gentileza informar po correta att pobox po box nfe send thursday june pm angela domingues moreira adecco recursos humanos angdom microsoft com subject fw regard po po gunaseelan jayaraj send thursday june po box nfe nfebr microso

hi try approve get approve red please help mesay corporate send friday june mesay abebe maq meabeb microsoft com subject require pende help pay within microsoft invoice pende go ms invoice sap vendor batch  would invoice company code invoice invoice sap interim approver discount discount value usd due receive arthur gensler jr associates june usd awe appreciate need via http cim send unmonitored alias
-----------
Invoice
dear po ap please reprocess attach po original po soon settle next wait recently approve regard mariana lopes adm datacenter operations latam microsoft cloud operations office tmf group behalf microsoft lopem microsoft
-----------
no
-----------
Invoice
hello prohelp three tie old show copy show local india alerted hope also look pos close try open unable need pay please open kimball garvin finance cct hr bldg kimball garvin microsoft com kristen mattie costales send wednesday june pm kimball garvin kimball garvin microsoft com subject pende gsmo hr pos old pende yet a

boa tarde karine voce ja tem uma posicao quanto data de pagamento da fatura vencida  desde ja agradecemos colocamo nos disposicao para que precisar atenciosamente luciana de campos rampi assistente de cobranca av julio de castilhos andar porto alegre tel de luciana de campos rampi enviada  quarta feira de junho de para brzap brazil brzap microsoft com karine goncalve dos santos kargon microsoft com luciana navarro lnavarro microsoft com pesc microsoft com pobox nfebr nfebr microsoft com cc caroline martins daitx cmartin uolinc fabio de oliveira barbosa fobarbosa uoldiveo com heitor kenji gakia hgakia uoldiveo com luciana rosa silva lrosa uolinc maicon cezar martelli mmartelli uolinc com mariane muller ribeiro mribeiro uolinc com marcel thimm fernandes de andrade uoldiveo com paula moreira noguez pnoguez silvia goncalve ferreira sferreira uoldiveo thais araujo de medeiros tmedeiros uoldiveo com assunto enc financeiro uol diveo aviso de pendencia vcto junho microsoft informatica ltda pri

hello please invoice asap one slightly high however limit code thank sarka jana demartini mailto demartini royalemma cz send cervna sarka kohoutova sarka kohoutova skype net kristyna petrackova axial personnel agency sro krpetr microsoft com cc plewkova royalemma cz subject faktura trika celenky summer day po swags dobry den sarko zde celkova faktura za summer day faktura za swags newcomers shosteskou vse vyresime odcizena lahev jeji honorar byl samozrejme odecten na slecnu poskytneme negativni reference agentury ktera nam ji doporucila bus nevhodne chovani ridice posoudit nemohu nebyla jsem toho doufam ze batoh dorazil vporadku kolegovi nechybelo nic zobsahu nezlobte se prosim mejte pohodovy vikend jana sarka kohoutova mailto sarka kohoutova skype net send friday june pm jana demartini kristyna petrackova axial sro subject faktura trika celenky summer day dobry den jani protoze po bylo extend tak na celou akci vc swags mela byt faktura dekuji jana demartini mailto demartini royalemma 

hi able ms approve please help chris amesbury corporate microsoft northeast account cp bif send thursday june pm chris amesbury chris amesbury microsoft com cc dootson dootson microsoft com subject require pende mh hello chris approval must do within ms want see current ecif dashboard michelle ifg cp ecif services analyst ms mo link initial cp ecif services lead tyanna lass tyal microsoft com tier cp operations kristi althoff kralth microsoft com tier ms cp lead murray oxley muoxle microsoft com chris amesbury send wednesday june pm cp bif services msusbif microsoft com cc dootson dootson microsoft com subject require pende approve chris amesbury microsoft jun pm cp bif services msusbif microsoft com write hello chris invoices project babcock note pende please go invoice approve jpg http getbif project_view html projectid want see current ecif dashboard michelle ifg cp ecif services analyst ms mo link jpg initial cp ecif services lead tyanna lass tyal microsoft com tier cp operations k

...

hi please see attach send nov payment po pay kindly advise thank kam sameera mohamed send wednesday june kamentha govender manpower kagove microsoft com cc enid lizamore enidl microsoft com subject fwd top certification outstanding overdue hey kam well never get pay please urgently check ap let know speak directly super embarrassed sam get outlook iosfrom billy elliott billy elliott top send wednesday june sameera mohamed enid lizamore cc marle hougaard subject top certification outstanding overdue good sam enid trust well receive overdue mandated overdue legal receive next wednesday want follow please confirm make next wednesday look forward feedback thankyou kindlykind regard billy elliott country south africa develop always top employers institute suite sovereign quay somerset road green point billy elliott top
-----------
Invoice
often get wanlin deloitte learn important hi aravind sg ap team good per understand understand control procedure chennai ap run unpresented stale cheque r

hola naty por favor nos ayuda que pasen mas dias gracias gonzalo vicencio send lunes de julio de support platam microsoft com natalia ocampo accenture nocam microsoft com natalia ocampo accenture nocam microsoft com rosa fuentes adecco recursos humanos rosaf microsoft com subject tkt urgente amex hi problem thanksgonzalo gonzalo vicencio dynamic excecutive gonzalo vicencio microsoft com skype govicenc microsoft com whatsapp send friday june gonzalo vicencio gonzalo vicencio microsoft com gonzalo vicencio gonzalo vicencio microsoft com natalia ocampo accenture nocam microsoft com natalia ocampo accenture nocam microsoft com rosa fuentes adecco recursos humanos rosaf microsoft com subject tkt urgente amex high hi rosa kindly inform able open please send normal let  know regard saranya yanamala microsoft one payable payable commit within meet inadequate please escalate latam pesc microsoft sla check invoice try need urgent try cim one stop portal query internal microsoft use important mic

answers topic saludos ing jose marcelo apena menor manager iws peru mcp mail japena iwsservices com calle las orquideas piso oficina san isidro lima peru conmutador http www com usa mexico peru colombia panama elperformance del equipo es necesario para logras las metas de jose marcelo apena menor enviado el lunes de junio de para platam platam microsoft com cc manuel apena mercedes mapena iwsservices com asunto tkt invoice pay non existent bank hi raghu impossible since scotiabank account exist currently open ago scotiabank exist correct correct iws servicio de rl de cv bbva bancomer bank interbank make sure saludos ing jose marcelo apena menor manager iws peru mcp mail japena iwsservices com calle las orquideas piso oficina san isidro lima peru conmutador http www com usa mexico peru colombia panama elperformance del equipo es necesario para logras las metas de platam mailto platam microsoft com enviado el lunes de junio de para jose marcelo apena menor japena iwsservices com asunto t

hi joseph would like follow update vendor  would follow bank technical  would org name program company code vendor  would cdi dealers inc name oem incentives regard kamille joy cartago infosys bpo ltd kamcar microsoft com work aoc oem channel incentive filinvest corporate alabang muntinlupa city metro manila philippines send tuesday june pm kamille joy cartago infosys bpo limited kamcar microsoft com cc berna mae bilbao infosys bpo limited bebilb microsoft com berna mae bilbao infosys bpo limited bebilb microsoft com berna mae bilbao infosys bpo limited bebilb microsoft com carina apetrior infosys bpo limited caapet microsoft com carina apetrior infosys bpo limited caapet microsoft com fredrick ariate infosys bpo limited fraria microsoft com fredrick ariate infosys bpo limited fraria microsoft joseph arockiya dass susai accenture josoos microsoft joseph arockiya dass susai accenture josoos microsoft com raymond connolly accenture raycon microsoft com raymond connolly accenture raycon m

hi receive invoice thank regards jackie jasvir barton brook street mailto jabart microsoft com send monday july pm jackie tan jackie tan lusia wahyu quadra ms indonesia ap wang chunmei accenture cc grp microsoft sg subject tkt indonesia credit tes hi jackie receive invoice yet ap try barton procurement services contractor microsoft office jabart microsoft com microsoft procurement subsequent emails topic set fully execute legally bind may contain confidential share third without prior write microsoft intend sender immediately microsoft limited company register england wales whose registered microsoft thames valley park reading rg wg jasvir barton brook street send june jackie tan jackie tan tes amm com jackie tan jackie tan tes amm com lusia wahyu quadra lwahyu microsoft com ms indonesia ap apid microsoft com wang chunmei accenture wangch microsoft com cc grp microsoft sg microsoft sg tes amm com subject tkt indonesia credit te add need close fiscal ap please see attach ca next ms ap p

In [ ]:
for long_string in data_lemmatized:
       #for number in list:
    #print(long_string)
    if re.compile('|'.join(search_list),re.IGNORECASE).search(long_string): #re.IGNORECASE is used to ignore case
        # Do Something if word is present    
        print("Invoice")
        print(long_string)
    else:
        print("no")
    print("-----------")